In [1]:
# Ensure project root (OpenCEP) is on sys.path for imports like `from base.Pattern import Pattern`
import sys, os, pathlib

nb_dir = (
    pathlib.Path(__file__).parent if "__file__" in globals() else pathlib.Path.cwd()
)
project_root = str((nb_dir / "..").resolve())
if project_root not in sys.path:
    sys.path.insert(0, project_root)

from datetime import timedelta
from CEP import CEP
from base.Pattern import Pattern
from base.PatternStructure import (
    SeqOperator,
    PrimitiveEventStructure,
    KleeneClosureOperator,
)
from condition.CompositeCondition import AndCondition
from condition.Condition import Variable, SimpleCondition
from condition.KCCondition import KCIndexCondition
from stream.FileStream import FileOutputStream
from stream.DataFrameStream import CitiBikeDataFrameInputStream
from plugin.citibike.CitiBike2 import (
    CitiBikeTripEventTypeClassifier,
    CitiBikeDataFormatter,
)
import test
from tree.PatternMatchStorage import TreeStorageParameters
from parallel.ParallelExecutionParameters import (
    DataParallelExecutionParametersHirzelAlgorithm,
)
from parallel.ParallelExecutionPlatforms import ParallelExecutionPlatforms
from plugin.citibike.RessourceConsumption import RessourceConsumption

monitor = RessourceConsumption()

def get_pattern(timedelta_minutes=31):
    citibikeHotPathsPattern = Pattern(
        SeqOperator(
            KleeneClosureOperator(PrimitiveEventStructure("CitiBikeTrip", "a"), max_size=5),
            PrimitiveEventStructure("CitiBikeTrip", "b"),
        ),
        AndCondition(
            KCIndexCondition(
                names={"a"},
                getattr_func=lambda x: x["bikeid"],
                relation_op=lambda a1, a2: a1 == a2,
                offset=-1,
            ),
            KCIndexCondition(
                names={"a"},
                getattr_func=lambda x: (
                    int(float(x["startstationid"])),
                    int(float(x["endstationid"])),
                ),
                relation_op=lambda a1, a2: a1[0] == a2[1],
                offset=-1,
            ),
            SimpleCondition(
                Variable("a", lambda x: x[-1]["bikeid"]),
                Variable("b", lambda x: x["bikeid"]),
                relation_op=lambda a, b: a == b,
            ),
            SimpleCondition(
                Variable("a", lambda x: int(float(x[-1]["endstationid"]))),
                Variable("b", lambda x: int(float(x["startstationid"]))),
                relation_op=lambda a, b: a == b,
            ),
            SimpleCondition(
                Variable("b", lambda x: int(float(x["endstationid"]))),
                relation_op=lambda end_id: str(end_id) in {"111111"},
            ),
        ),
        timedelta(minutes=timedelta_minutes),
    )
    return citibikeHotPathsPattern

#### 10% of baseline = 0.01 latency bound

In [2]:
input_file = "../test/EventFiles/201901-citibike-tripdata-1-fabricated-original.csv"
output_file = "output_citibike_10pct_of_baseline.txt"

citibikeHotPathsPattern = get_pattern(timedelta_minutes=31)
load_shedding_threshold = 30  # when to start load shedding - length of partial match array
load_shedding_drop_rate = 0.1  # how many matches to drop when load shedding is active
latency_bound = 0.01  # in seconds


load_shedding_params = TreeStorageParameters(
    sort_storage=True,
    enable_load_shedding=True,
    load_shedding_threshold=load_shedding_threshold,
    load_shedding_drop_rate=load_shedding_drop_rate,
    load_shedding_strategy="oldest",
    clean_up_interval=10,
    latency_bound=latency_bound,
)
dp_params = DataParallelExecutionParametersHirzelAlgorithm(
    platform=ParallelExecutionPlatforms.THREADING,
    units_number=12,  # how many threads
    key="bikeid",
)
cep = CEP([citibikeHotPathsPattern], parallel_execution_params=dp_params, storage_params=load_shedding_params )

events = CitiBikeDataFrameInputStream(
    input_file,
    timestamp_column="starttime",
)

monitor.run(
    cep.run,
    events,
    FileOutputStream("../test/demo/Matches/project_results", output_file),
    CitiBikeDataFormatter(),
)

Creating evaluation manager...
 - Parallel execution: <parallel.ParallelExecutionParameters.DataParallelExecutionParametersHirzelAlgorithm object at 0x10d0651c0>
 - Storage: TreeStorageParameters(sort_storage=True, attributes_priorities={}, clean_up_interval=10, prioritize_sorting_by_timestamp=True, enable_load_shedding=True, load_shedding_threshold=30, load_shedding_drop_rate=0.1, load_shedding_strategy=oldest,latency_bound=0.01)
 - Using ParallelExecutionModes.DATA_PARALLELISM execution mode
Tree calling create_storage_unit with storage_params: TreeStorageParameters(sort_storage=True, attributes_priorities={}, clean_up_interval=10, prioritize_sorting_by_timestamp=True, enable_load_shedding=True, load_shedding_threshold=30, load_shedding_drop_rate=0.1, load_shedding_strategy=oldest,latency_bound=0.01)
LeafNode.create_storage_unit called with storage_params: TreeStorageParameters(sort_storage=True, attributes_priorities={}, clean_up_interval=10, prioritize_sorting_by_timestamp=True, en

Exception in thread Thread-6 (_run):
Traceback (most recent call last):
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1073, in _bootstrap_inner
    self.run()
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/venv/lib/python3.12/site-packages/ipykernel/ipkernel.py", line 772, in run_closure
    _threading_Thread_run(self)
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1010, in run
    self._target(*self._args, **self._kwargs)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/data_parallel/DataParallelExecutionAlgorithm.py", line 119, in _run
    evaluation_manager.eval(events, matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/manager/SequentialEvaluationManager.py", line 32, in eval
    self.__eval_mechanism.eval(event_stream, pattern_matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/tree/evaluation/

computed currlat 1.666775
Found match: {'tripduration': '73', 'starttime': 2019-01-08 13:11:45.406000, 'stoptime': 2019-01-08 13:12:58.484000, 'startstationid': '259', 'endstationid': '427', 'bikeid': '33615', 'eventid': 247450}
{'tripduration': '1290', 'starttime': 2019-01-08 13:13:02.735000, 'stoptime': 2019-01-08 13:34:33.205000, 'startstationid': '427', 'endstationid': '111111', 'bikeid': '33615', 'eventid': 247476}


event count 248701 598.82857575
we are updating event count 249000
we are updating event count 250000
computed currlat 1.666775
Found match: {'tripduration': '163', 'starttime': 2019-01-08 14:08:28.422000, 'stoptime': 2019-01-08 14:11:11.766000, 'startstationid': '503', 'endstationid': '3139', 'bikeid': '15603', 'eventid': 249079}
{'tripduration': '835', 'starttime': 2019-01-08 14:11:11.810000, 'stoptime': 2019-01-08 14:25:06.941000, 'startstationid': '3139', 'endstationid': '111111', 'bikeid': '15603', 'eventid': 249168}


event count 250255 601.82003225
we are updat

Exception in thread Thread-11 (_run):
Traceback (most recent call last):
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1073, in _bootstrap_inner
    self.run()
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/venv/lib/python3.12/site-packages/ipykernel/ipkernel.py", line 772, in run_closure
    _threading_Thread_run(self)
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1010, in run
    self._target(*self._args, **self._kwargs)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/data_parallel/DataParallelExecutionAlgorithm.py", line 119, in _run
    evaluation_manager.eval(events, matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/manager/SequentialEvaluationManager.py", line 32, in eval
    self.__eval_mechanism.eval(event_stream, pattern_matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/tree/evaluation

computed currlat 1.666775
Found match: {'tripduration': '152', 'starttime': 2019-01-10 13:18:43.882000, 'stoptime': 2019-01-10 13:21:16.782000, 'startstationid': '3431', 'endstationid': '517', 'bikeid': '35111', 'eventid': 334350}
{'tripduration': '475', 'starttime': 2019-01-10 13:21:17.431000, 'stoptime': 2019-01-10 13:29:12.840000, 'startstationid': '517', 'endstationid': '111111', 'bikeid': '35111', 'eventid': 334422}


event count 332641 760.820830375
computed currlat 1.666775
Found match: {'tripduration': '182', 'starttime': 2019-01-10 14:53:11.421000, 'stoptime': 2019-01-10 14:56:13.913000, 'startstationid': '3463', 'endstationid': '285', 'bikeid': '34414', 'eventid': 336950}
{'tripduration': '468', 'starttime': 2019-01-10 14:56:20.370000, 'stoptime': 2019-01-10 15:04:09.293000, 'startstationid': '285', 'endstationid': '111111', 'bikeid': '34414', 'eventid': 337029}


event count 332836 761.20687175
we are updating event count 333000
computed currlat 1.666775
Found match: {'tripd

...

Exception in thread Thread-12 (_run):
Traceback (most recent call last):
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1073, in _bootstrap_inner
    self.run()
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/venv/lib/python3.12/site-packages/ipykernel/ipkernel.py", line 772, in run_closure
    _threading_Thread_run(self)
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1010, in run
    self._target(*self._args, **self._kwargs)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/data_parallel/DataParallelExecutionAlgorithm.py", line 119, in _run
    evaluation_manager.eval(events, matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/manager/SequentialEvaluationManager.py", line 32, in eval
    self.__eval_mechanism.eval(event_stream, pattern_matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/tree/evaluation

we are updating event count 635000
computed currlat 0.078153
Found match: {'tripduration': '191', 'starttime': 2019-01-26 19:09:51.183000, 'stoptime': 2019-01-26 19:13:02.364000, 'startstationid': '465', 'endstationid': '529', 'bikeid': '35741', 'eventid': 823050}
{'tripduration': '452', 'starttime': 2019-01-26 19:13:06.155000, 'stoptime': 2019-01-26 19:20:38.540000, 'startstationid': '529', 'endstationid': '111111', 'bikeid': '35741', 'eventid': 823138}


event count 635258 1361.527824291
computed currlat 0.078153
Found match: {'tripduration': '106', 'starttime': 2019-01-26 11:51:12.837000, 'stoptime': 2019-01-26 11:52:59.121000, 'startstationid': '3321', 'endstationid': '3315', 'bikeid': '33251', 'eventid': 807850}
{'tripduration': '407', 'starttime': 2019-01-26 11:52:59.756000, 'stoptime': 2019-01-26 11:59:47.256000, 'startstationid': '3315', 'endstationid': '111111', 'bikeid': '33251', 'eventid': 807935}


event count 635428 1361.863752
computed currlat 0.078153
Found match: {'trip

Exception in thread Thread-9 (_run):
Traceback (most recent call last):
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1073, in _bootstrap_inner
    self.run()
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/venv/lib/python3.12/site-packages/ipykernel/ipkernel.py", line 772, in run_closure
    _threading_Thread_run(self)
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1010, in run
    self._target(*self._args, **self._kwargs)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/data_parallel/DataParallelExecutionAlgorithm.py", line 119, in _run
    evaluation_manager.eval(events, matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/manager/SequentialEvaluationManager.py", line 32, in eval
    self.__eval_mechanism.eval(event_stream, pattern_matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/tree/evaluation/

computed currlat 0.687878
Found match: {'tripduration': '216', 'starttime': 2019-01-28 12:21:47.953000, 'stoptime': 2019-01-28 12:25:24.421000, 'startstationid': '426', 'endstationid': '82', 'bikeid': '28235', 'eventid': 871043}
{'tripduration': '303', 'starttime': 2019-01-28 12:25:25.376000, 'stoptime': 2019-01-28 12:30:28.727000, 'startstationid': '82', 'endstationid': '111111', 'bikeid': '28235', 'eventid': 871128}


event count 668675 1428.610824958
computed currlat 0.687878
Found match: {'tripduration': '169', 'starttime': 2019-01-28 12:44:57.703000, 'stoptime': 2019-01-28 12:47:47.344000, 'startstationid': '3454', 'endstationid': '3081', 'bikeid': '35387', 'eventid': 871600}
{'tripduration': '702', 'starttime': 2019-01-28 12:47:48.190000, 'stoptime': 2019-01-28 12:59:30.981000, 'startstationid': '3081', 'endstationid': '111111', 'bikeid': '35387', 'eventid': 871661}


event count 668939 1429.144549
we are updating event count 669000
computed currlat 0.687878
Found match: {'tripdu

1411.218123

### 30% of baseline

In [2]:
input_file = "../test/EventFiles/201901-citibike-tripdata-1-fabricated-original.csv"
output_file = "output_citibike_30pct_of_baseline.txt"

citibikeHotPathsPattern = get_pattern(timedelta_minutes=31)
load_shedding_threshold = 30  # when to start load shedding - length of partial match array
load_shedding_drop_rate = 0.1  # how many matches to drop when load shedding is active
latency_bound = 0.03  # in seconds


load_shedding_params = TreeStorageParameters(
    sort_storage=True,
    enable_load_shedding=True,
    load_shedding_threshold=load_shedding_threshold,
    load_shedding_drop_rate=load_shedding_drop_rate,
    load_shedding_strategy="oldest",
    clean_up_interval=10,
    latency_bound=latency_bound,
)
dp_params = DataParallelExecutionParametersHirzelAlgorithm(
    platform=ParallelExecutionPlatforms.THREADING,
    units_number=12,  # how many threads
    key="bikeid",
)
cep = CEP([citibikeHotPathsPattern], parallel_execution_params=dp_params, storage_params=load_shedding_params )

events = CitiBikeDataFrameInputStream(
    input_file,
    timestamp_column="starttime",
)

monitor.run(
    cep.run,
    events,
    FileOutputStream("../test/demo/Matches/project_results", output_file),
    CitiBikeDataFormatter(),
)

Creating evaluation manager...
 - Parallel execution: <parallel.ParallelExecutionParameters.DataParallelExecutionParametersHirzelAlgorithm object at 0x11dc37560>
 - Storage: TreeStorageParameters(sort_storage=True, attributes_priorities={}, clean_up_interval=10, prioritize_sorting_by_timestamp=True, enable_load_shedding=True, load_shedding_threshold=30, load_shedding_drop_rate=0.1, load_shedding_strategy=oldest,latency_bound=0.03)
 - Using ParallelExecutionModes.DATA_PARALLELISM execution mode
Tree calling create_storage_unit with storage_params: TreeStorageParameters(sort_storage=True, attributes_priorities={}, clean_up_interval=10, prioritize_sorting_by_timestamp=True, enable_load_shedding=True, load_shedding_threshold=30, load_shedding_drop_rate=0.1, load_shedding_strategy=oldest,latency_bound=0.03)
LeafNode.create_storage_unit called with storage_params: TreeStorageParameters(sort_storage=True, attributes_priorities={}, clean_up_interval=10, prioritize_sorting_by_timestamp=True, en

Exception in thread Thread-6 (_run):
Traceback (most recent call last):
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1073, in _bootstrap_inner
    self.run()
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/venv/lib/python3.12/site-packages/ipykernel/ipkernel.py", line 772, in run_closure
    _threading_Thread_run(self)
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1010, in run
    self._target(*self._args, **self._kwargs)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/data_parallel/DataParallelExecutionAlgorithm.py", line 119, in _run
    evaluation_manager.eval(events, matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/manager/SequentialEvaluationManager.py", line 32, in eval
    self.__eval_mechanism.eval(event_stream, pattern_matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/tree/evaluation/

computed currlat 1.648512
Found match: {'tripduration': '73', 'starttime': 2019-01-08 13:11:45.406000, 'stoptime': 2019-01-08 13:12:58.484000, 'startstationid': '259', 'endstationid': '427', 'bikeid': '33615', 'eventid': 247450}
{'tripduration': '1290', 'starttime': 2019-01-08 13:13:02.735000, 'stoptime': 2019-01-08 13:34:33.205000, 'startstationid': '427', 'endstationid': '111111', 'bikeid': '33615', 'eventid': 247476}


event count 248712 2535.320441291
we are updating event count 249000
computed currlat 1.648512
Found match: {'tripduration': '166', 'starttime': 2019-01-08 12:36:46.278000, 'stoptime': 2019-01-08 12:39:32.973000, 'startstationid': '3435', 'endstationid': '251', 'bikeid': '15679', 'eventid': 246400}
{'tripduration': '451', 'starttime': 2019-01-08 12:39:34.591000, 'stoptime': 2019-01-08 12:47:05.674000, 'startstationid': '251', 'endstationid': '111111', 'bikeid': '15679', 'eventid': 246494}


event count 249858 2537.574912208
we are updating event count 250000
computed 

Exception in thread Thread-11 (_run):
Traceback (most recent call last):
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1073, in _bootstrap_inner
    self.run()
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/venv/lib/python3.12/site-packages/ipykernel/ipkernel.py", line 772, in run_closure
    _threading_Thread_run(self)
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1010, in run
    self._target(*self._args, **self._kwargs)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/data_parallel/DataParallelExecutionAlgorithm.py", line 119, in _run
    evaluation_manager.eval(events, matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/manager/SequentialEvaluationManager.py", line 32, in eval
    self.__eval_mechanism.eval(event_stream, pattern_matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/tree/evaluation

computed currlat 1.648512
Found match: {'tripduration': '152', 'starttime': 2019-01-10 13:18:43.882000, 'stoptime': 2019-01-10 13:21:16.782000, 'startstationid': '3431', 'endstationid': '517', 'bikeid': '35111', 'eventid': 334350}
{'tripduration': '475', 'starttime': 2019-01-10 13:21:17.431000, 'stoptime': 2019-01-10 13:29:12.840000, 'startstationid': '517', 'endstationid': '111111', 'bikeid': '35111', 'eventid': 334422}


event count 332753 2701.659433958
computed currlat 1.648512
Found match: {'tripduration': '182', 'starttime': 2019-01-10 14:53:11.421000, 'stoptime': 2019-01-10 14:56:13.913000, 'startstationid': '3463', 'endstationid': '285', 'bikeid': '34414', 'eventid': 336950}
{'tripduration': '468', 'starttime': 2019-01-10 14:56:20.370000, 'stoptime': 2019-01-10 15:04:09.293000, 'startstationid': '285', 'endstationid': '111111', 'bikeid': '34414', 'eventid': 337029}


event count 332826 2701.826950541
we are updating event count 333000
computed currlat 1.648512
Found match: {'tr

...

Exception in thread Thread-12 (_run):
Traceback (most recent call last):
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1073, in _bootstrap_inner
    self.run()
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/venv/lib/python3.12/site-packages/ipykernel/ipkernel.py", line 772, in run_closure
    _threading_Thread_run(self)
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1010, in run
    self._target(*self._args, **self._kwargs)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/data_parallel/DataParallelExecutionAlgorithm.py", line 119, in _run
    evaluation_manager.eval(events, matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/manager/SequentialEvaluationManager.py", line 32, in eval
    self.__eval_mechanism.eval(event_stream, pattern_matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/tree/evaluation

we are updating event count 635000
computed currlat 0.707026
Found match: {'tripduration': '191', 'starttime': 2019-01-26 19:09:51.183000, 'stoptime': 2019-01-26 19:13:02.364000, 'startstationid': '465', 'endstationid': '529', 'bikeid': '35741', 'eventid': 823050}
{'tripduration': '452', 'starttime': 2019-01-26 19:13:06.155000, 'stoptime': 2019-01-26 19:20:38.540000, 'startstationid': '529', 'endstationid': '111111', 'bikeid': '35741', 'eventid': 823138}


event count 635174 3305.007947
computed currlat 0.707026
Found match: {'tripduration': '106', 'starttime': 2019-01-26 11:51:12.837000, 'stoptime': 2019-01-26 11:52:59.121000, 'startstationid': '3321', 'endstationid': '3315', 'bikeid': '33251', 'eventid': 807850}
{'tripduration': '407', 'starttime': 2019-01-26 11:52:59.756000, 'stoptime': 2019-01-26 11:59:47.256000, 'startstationid': '3315', 'endstationid': '111111', 'bikeid': '33251', 'eventid': 807935}


event count 635481 3305.620623958
computed currlat 0.707026
Found match: {'trip

Exception in thread Thread-9 (_run):
Traceback (most recent call last):
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1073, in _bootstrap_inner
    self.run()
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/venv/lib/python3.12/site-packages/ipykernel/ipkernel.py", line 772, in run_closure
    _threading_Thread_run(self)
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1010, in run
    self._target(*self._args, **self._kwargs)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/data_parallel/DataParallelExecutionAlgorithm.py", line 119, in _run
    evaluation_manager.eval(events, matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/manager/SequentialEvaluationManager.py", line 32, in eval
    self.__eval_mechanism.eval(event_stream, pattern_matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/tree/evaluation/

computed currlat 0.707026
Found match: {'tripduration': '216', 'starttime': 2019-01-28 12:21:47.953000, 'stoptime': 2019-01-28 12:25:24.421000, 'startstationid': '426', 'endstationid': '82', 'bikeid': '28235', 'eventid': 871043}
{'tripduration': '303', 'starttime': 2019-01-28 12:25:25.376000, 'stoptime': 2019-01-28 12:30:28.727000, 'startstationid': '82', 'endstationid': '111111', 'bikeid': '28235', 'eventid': 871128}


event count 668720 3372.724155083
computed currlat 0.707026
Found match: {'tripduration': '169', 'starttime': 2019-01-28 12:44:57.703000, 'stoptime': 2019-01-28 12:47:47.344000, 'startstationid': '3454', 'endstationid': '3081', 'bikeid': '35387', 'eventid': 871600}
{'tripduration': '702', 'starttime': 2019-01-28 12:47:48.190000, 'stoptime': 2019-01-28 12:59:30.981000, 'startstationid': '3081', 'endstationid': '111111', 'bikeid': '35387', 'eventid': 871661}


event count 668977 3373.281660833
we are updating event count 669000
computed currlat 0.707026
Found match: {'tri

1428.87422

### 50% of baseline

In [2]:
input_file = "../test/EventFiles/201901-citibike-tripdata-1-fabricated-original.csv"
output_file = "output_citibike_50pct_of_baseline.txt"

citibikeHotPathsPattern = get_pattern(timedelta_minutes=31)
load_shedding_threshold = 30  # when to start load shedding - length of partial match array
load_shedding_drop_rate = 0.1  # how many matches to drop when load shedding is active
latency_bound = 0.05  # in seconds


load_shedding_params = TreeStorageParameters(
    sort_storage=True,
    enable_load_shedding=True,
    load_shedding_threshold=load_shedding_threshold,
    load_shedding_drop_rate=load_shedding_drop_rate,
    load_shedding_strategy="oldest",
    clean_up_interval=10,
    latency_bound=latency_bound,
)
dp_params = DataParallelExecutionParametersHirzelAlgorithm(
    platform=ParallelExecutionPlatforms.THREADING,
    units_number=12,  # how many threads
    key="bikeid",
)
cep = CEP([citibikeHotPathsPattern], parallel_execution_params=dp_params, storage_params=load_shedding_params )

events = CitiBikeDataFrameInputStream(
    input_file,
    timestamp_column="starttime",
)

monitor.run(
    cep.run,
    events,
    FileOutputStream("../test/demo/Matches/project_results", output_file),
    CitiBikeDataFormatter(),
)

Creating evaluation manager...
 - Parallel execution: <parallel.ParallelExecutionParameters.DataParallelExecutionParametersHirzelAlgorithm object at 0x118cf35f0>
 - Storage: TreeStorageParameters(sort_storage=True, attributes_priorities={}, clean_up_interval=10, prioritize_sorting_by_timestamp=True, enable_load_shedding=True, load_shedding_threshold=30, load_shedding_drop_rate=0.1, load_shedding_strategy=oldest,latency_bound=0.05)
 - Using ParallelExecutionModes.DATA_PARALLELISM execution mode
Tree calling create_storage_unit with storage_params: TreeStorageParameters(sort_storage=True, attributes_priorities={}, clean_up_interval=10, prioritize_sorting_by_timestamp=True, enable_load_shedding=True, load_shedding_threshold=30, load_shedding_drop_rate=0.1, load_shedding_strategy=oldest,latency_bound=0.05)
LeafNode.create_storage_unit called with storage_params: TreeStorageParameters(sort_storage=True, attributes_priorities={}, clean_up_interval=10, prioritize_sorting_by_timestamp=True, en

KeyboardInterrupt: 

### 70pct of baseline

In [3]:
input_file = "../test/EventFiles/201901-citibike-tripdata-1-fabricated-original.csv"
output_file = "output_citibike_70pct_of_baseline.txt"

citibikeHotPathsPattern = get_pattern(timedelta_minutes=31)
load_shedding_threshold = 30  # when to start load shedding - length of partial match array
load_shedding_drop_rate = 0.1  # how many matches to drop when load shedding is active
latency_bound = 0.07  # in seconds


load_shedding_params = TreeStorageParameters(
    sort_storage=True,
    enable_load_shedding=True,
    load_shedding_threshold=load_shedding_threshold,
    load_shedding_drop_rate=load_shedding_drop_rate,
    load_shedding_strategy="oldest",
    clean_up_interval=10,
    latency_bound=latency_bound,
)
dp_params = DataParallelExecutionParametersHirzelAlgorithm(
    platform=ParallelExecutionPlatforms.THREADING,
    units_number=12,  # how many threads
    key="bikeid",
)
cep = CEP([citibikeHotPathsPattern], parallel_execution_params=dp_params, storage_params=load_shedding_params )

events = CitiBikeDataFrameInputStream(
    input_file,
    timestamp_column="starttime",
)

monitor.run(
    cep.run,
    events,
    FileOutputStream("../test/demo/Matches/project_results", output_file),
    CitiBikeDataFormatter(),
)

Creating evaluation manager...
 - Parallel execution: <parallel.ParallelExecutionParameters.DataParallelExecutionParametersHirzelAlgorithm object at 0x127fb54c0>
 - Storage: TreeStorageParameters(sort_storage=True, attributes_priorities={}, clean_up_interval=10, prioritize_sorting_by_timestamp=True, enable_load_shedding=True, load_shedding_threshold=30, load_shedding_drop_rate=0.1, load_shedding_strategy=oldest,latency_bound=0.07)
 - Using ParallelExecutionModes.DATA_PARALLELISM execution mode
Tree calling create_storage_unit with storage_params: TreeStorageParameters(sort_storage=True, attributes_priorities={}, clean_up_interval=10, prioritize_sorting_by_timestamp=True, enable_load_shedding=True, load_shedding_threshold=30, load_shedding_drop_rate=0.1, load_shedding_strategy=oldest,latency_bound=0.07)
LeafNode.create_storage_unit called with storage_params: TreeStorageParameters(sort_storage=True, attributes_priorities={}, clean_up_interval=10, prioritize_sorting_by_timestamp=True, en

Exception in thread Thread-6 (_run):
Traceback (most recent call last):
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1073, in _bootstrap_inner
    self.run()
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/venv/lib/python3.12/site-packages/ipykernel/ipkernel.py", line 772, in run_closure
    _threading_Thread_run(self)
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1010, in run
    self._target(*self._args, **self._kwargs)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/data_parallel/DataParallelExecutionAlgorithm.py", line 119, in _run
    evaluation_manager.eval(events, matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/manager/SequentialEvaluationManager.py", line 32, in eval
    self.__eval_mechanism.eval(event_stream, pattern_matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/tree/evaluation/

computed currlat 1.634319
Found match: {'tripduration': '73', 'starttime': 2019-01-08 13:11:45.406000, 'stoptime': 2019-01-08 13:12:58.484000, 'startstationid': '259', 'endstationid': '427', 'bikeid': '33615', 'eventid': 247450}
{'tripduration': '1290', 'starttime': 2019-01-08 13:13:02.735000, 'stoptime': 2019-01-08 13:34:33.205000, 'startstationid': '427', 'endstationid': '111111', 'bikeid': '33615', 'eventid': 247476}


event count 248742 5809.78197575
we are updating event count 249000
we are updating event count 250000
computed currlat 1.634319
Found match: {'tripduration': '163', 'starttime': 2019-01-08 14:08:28.422000, 'stoptime': 2019-01-08 14:11:11.766000, 'startstationid': '503', 'endstationid': '3139', 'bikeid': '15603', 'eventid': 249079}
{'tripduration': '835', 'starttime': 2019-01-08 14:11:11.810000, 'stoptime': 2019-01-08 14:25:06.941000, 'startstationid': '3139', 'endstationid': '111111', 'bikeid': '15603', 'eventid': 249168}


event count 250296 5812.847921292
we are up

Exception in thread Thread-11 (_run):
Traceback (most recent call last):
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1073, in _bootstrap_inner
    self.run()
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/venv/lib/python3.12/site-packages/ipykernel/ipkernel.py", line 772, in run_closure
    _threading_Thread_run(self)
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1010, in run
    self._target(*self._args, **self._kwargs)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/data_parallel/DataParallelExecutionAlgorithm.py", line 119, in _run
    evaluation_manager.eval(events, matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/manager/SequentialEvaluationManager.py", line 32, in eval
    self.__eval_mechanism.eval(event_stream, pattern_matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/tree/evaluation

computed currlat 1.634319
Found match: {'tripduration': '152', 'starttime': 2019-01-10 13:18:43.882000, 'stoptime': 2019-01-10 13:21:16.782000, 'startstationid': '3431', 'endstationid': '517', 'bikeid': '35111', 'eventid': 334350}
{'tripduration': '475', 'starttime': 2019-01-10 13:21:17.431000, 'stoptime': 2019-01-10 13:29:12.840000, 'startstationid': '517', 'endstationid': '111111', 'bikeid': '35111', 'eventid': 334422}


event count 332595 5976.041917167
computed currlat 1.634319
Found match: {'tripduration': '182', 'starttime': 2019-01-10 14:53:11.421000, 'stoptime': 2019-01-10 14:56:13.913000, 'startstationid': '3463', 'endstationid': '285', 'bikeid': '34414', 'eventid': 336950}
{'tripduration': '468', 'starttime': 2019-01-10 14:56:20.370000, 'stoptime': 2019-01-10 15:04:09.293000, 'startstationid': '285', 'endstationid': '111111', 'bikeid': '34414', 'eventid': 337029}


event count 332893 5976.622394083
we are updating event count 333000
computed currlat 1.634319
Found match: {'tr

...

Exception in thread Thread-12 (_run):
Traceback (most recent call last):
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1073, in _bootstrap_inner
    self.run()
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/venv/lib/python3.12/site-packages/ipykernel/ipkernel.py", line 772, in run_closure
    _threading_Thread_run(self)
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1010, in run
    self._target(*self._args, **self._kwargs)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/data_parallel/DataParallelExecutionAlgorithm.py", line 119, in _run
    evaluation_manager.eval(events, matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/manager/SequentialEvaluationManager.py", line 32, in eval
    self.__eval_mechanism.eval(event_stream, pattern_matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/tree/evaluation

we are updating event count 635000
computed currlat 33.04141
Found match: {'tripduration': '191', 'starttime': 2019-01-26 19:09:51.183000, 'stoptime': 2019-01-26 19:13:02.364000, 'startstationid': '465', 'endstationid': '529', 'bikeid': '35741', 'eventid': 823050}
{'tripduration': '452', 'starttime': 2019-01-26 19:13:06.155000, 'stoptime': 2019-01-26 19:20:38.540000, 'startstationid': '529', 'endstationid': '111111', 'bikeid': '35741', 'eventid': 823138}


event count 635199 6586.500615875
computed currlat 33.04141
Found match: {'tripduration': '106', 'starttime': 2019-01-26 11:51:12.837000, 'stoptime': 2019-01-26 11:52:59.121000, 'startstationid': '3321', 'endstationid': '3315', 'bikeid': '33251', 'eventid': 807850}
{'tripduration': '407', 'starttime': 2019-01-26 11:52:59.756000, 'stoptime': 2019-01-26 11:59:47.256000, 'startstationid': '3315', 'endstationid': '111111', 'bikeid': '33251', 'eventid': 807935}


event count 635332 6586.771447583
computed currlat 33.04141
Found match: {'t

Exception in thread Thread-9 (_run):
Traceback (most recent call last):
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1073, in _bootstrap_inner
    self.run()
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/venv/lib/python3.12/site-packages/ipykernel/ipkernel.py", line 772, in run_closure
    _threading_Thread_run(self)
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1010, in run
    self._target(*self._args, **self._kwargs)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/data_parallel/DataParallelExecutionAlgorithm.py", line 119, in _run
    evaluation_manager.eval(events, matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/manager/SequentialEvaluationManager.py", line 32, in eval
    self.__eval_mechanism.eval(event_stream, pattern_matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/tree/evaluation/

computed currlat 0.788794
Found match: {'tripduration': '169', 'starttime': 2019-01-28 12:44:57.703000, 'stoptime': 2019-01-28 12:47:47.344000, 'startstationid': '3454', 'endstationid': '3081', 'bikeid': '35387', 'eventid': 871600}
{'tripduration': '702', 'starttime': 2019-01-28 12:47:48.190000, 'stoptime': 2019-01-28 12:59:30.981000, 'startstationid': '3081', 'endstationid': '111111', 'bikeid': '35387', 'eventid': 871661}


event count 668858 6655.657661333
we are updating event count 669000
computed currlat 0.788794
Found match: {'tripduration': '111', 'starttime': 2019-01-28 20:17:08.240000, 'stoptime': 2019-01-28 20:18:59.317000, 'startstationid': '447', 'endstationid': '423', 'bikeid': '29749', 'eventid': 889500}
{'tripduration': '250', 'starttime': 2019-01-28 20:18:59.677000, 'stoptime': 2019-01-28 20:23:10.583000, 'startstationid': '423', 'endstationid': '111111', 'bikeid': '29749', 'eventid': 889553}


event count 669290 6656.540728958
computed currlat 0.788794
computed currlat

1479.378412

### 90% of baseline

In [2]:
input_file = "../test/EventFiles/201901-citibike-tripdata-1-fabricated-original.csv"
output_file = "output_citibike_90pct_of_baseline.txt"

citibikeHotPathsPattern = get_pattern(timedelta_minutes=31)
load_shedding_threshold = 30  # when to start load shedding - length of partial match array
load_shedding_drop_rate = 0.1  # how many matches to drop when load shedding is active
latency_bound = 0.09  # in seconds


load_shedding_params = TreeStorageParameters(
    sort_storage=True,
    enable_load_shedding=True,
    load_shedding_threshold=load_shedding_threshold,
    load_shedding_drop_rate=load_shedding_drop_rate,
    load_shedding_strategy="oldest",
    clean_up_interval=10,
    latency_bound=latency_bound,
)
dp_params = DataParallelExecutionParametersHirzelAlgorithm(
    platform=ParallelExecutionPlatforms.THREADING,
    units_number=12,  # how many threads
    key="bikeid",
)
cep = CEP([citibikeHotPathsPattern], parallel_execution_params=dp_params, storage_params=load_shedding_params )

events = CitiBikeDataFrameInputStream(
    input_file,
    timestamp_column="starttime",
)

monitor.run(
    cep.run,
    events,
    FileOutputStream("../test/demo/Matches/project_results", output_file),
    CitiBikeDataFormatter(),
)

Creating evaluation manager...
 - Parallel execution: <parallel.ParallelExecutionParameters.DataParallelExecutionParametersHirzelAlgorithm object at 0x11b5674a0>
 - Storage: TreeStorageParameters(sort_storage=True, attributes_priorities={}, clean_up_interval=10, prioritize_sorting_by_timestamp=True, enable_load_shedding=True, load_shedding_threshold=30, load_shedding_drop_rate=0.1, load_shedding_strategy=oldest,latency_bound=0.09)
 - Using ParallelExecutionModes.DATA_PARALLELISM execution mode
Tree calling create_storage_unit with storage_params: TreeStorageParameters(sort_storage=True, attributes_priorities={}, clean_up_interval=10, prioritize_sorting_by_timestamp=True, enable_load_shedding=True, load_shedding_threshold=30, load_shedding_drop_rate=0.1, load_shedding_strategy=oldest,latency_bound=0.09)
LeafNode.create_storage_unit called with storage_params: TreeStorageParameters(sort_storage=True, attributes_priorities={}, clean_up_interval=10, prioritize_sorting_by_timestamp=True, en

Exception in thread Thread-6 (_run):
Traceback (most recent call last):
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1073, in _bootstrap_inner
    self.run()
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/venv/lib/python3.12/site-packages/ipykernel/ipkernel.py", line 772, in run_closure
    _threading_Thread_run(self)
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1010, in run
    self._target(*self._args, **self._kwargs)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/data_parallel/DataParallelExecutionAlgorithm.py", line 119, in _run
    evaluation_manager.eval(events, matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/manager/SequentialEvaluationManager.py", line 32, in eval
    self.__eval_mechanism.eval(event_stream, pattern_matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/tree/evaluation/

computed currlat 1.690056
Found match: {'tripduration': '73', 'starttime': 2019-01-08 13:11:45.406000, 'stoptime': 2019-01-08 13:12:58.484000, 'startstationid': '259', 'endstationid': '427', 'bikeid': '33615', 'eventid': 247450}
{'tripduration': '1290', 'starttime': 2019-01-08 13:13:02.735000, 'stoptime': 2019-01-08 13:34:33.205000, 'startstationid': '427', 'endstationid': '111111', 'bikeid': '33615', 'eventid': 247476}


event count 248629 7356.367323541
we are updating event count 249000
we are updating event count 250000
computed currlat 1.690056
Found match: {'tripduration': '163', 'starttime': 2019-01-08 14:08:28.422000, 'stoptime': 2019-01-08 14:11:11.766000, 'startstationid': '503', 'endstationid': '3139', 'bikeid': '15603', 'eventid': 249079}
{'tripduration': '835', 'starttime': 2019-01-08 14:11:11.810000, 'stoptime': 2019-01-08 14:25:06.941000, 'startstationid': '3139', 'endstationid': '111111', 'bikeid': '15603', 'eventid': 249168}


event count 250183 7359.411860541
we are u

Exception in thread Thread-11 (_run):
Traceback (most recent call last):
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1073, in _bootstrap_inner
    self.run()
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/venv/lib/python3.12/site-packages/ipykernel/ipkernel.py", line 772, in run_closure
    _threading_Thread_run(self)
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1010, in run
    self._target(*self._args, **self._kwargs)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/data_parallel/DataParallelExecutionAlgorithm.py", line 119, in _run
    evaluation_manager.eval(events, matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/manager/SequentialEvaluationManager.py", line 32, in eval
    self.__eval_mechanism.eval(event_stream, pattern_matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/tree/evaluation

computed currlat 1.690056
Found match: {'tripduration': '152', 'starttime': 2019-01-10 13:18:43.882000, 'stoptime': 2019-01-10 13:21:16.782000, 'startstationid': '3431', 'endstationid': '517', 'bikeid': '35111', 'eventid': 334350}
{'tripduration': '475', 'starttime': 2019-01-10 13:21:17.431000, 'stoptime': 2019-01-10 13:29:12.840000, 'startstationid': '517', 'endstationid': '111111', 'bikeid': '35111', 'eventid': 334422}


event count 332652 7522.075591916
computed currlat 1.690056
Found match: {'tripduration': '182', 'starttime': 2019-01-10 14:53:11.421000, 'stoptime': 2019-01-10 14:56:13.913000, 'startstationid': '3463', 'endstationid': '285', 'bikeid': '34414', 'eventid': 336950}
{'tripduration': '468', 'starttime': 2019-01-10 14:56:20.370000, 'stoptime': 2019-01-10 15:04:09.293000, 'startstationid': '285', 'endstationid': '111111', 'bikeid': '34414', 'eventid': 337029}


event count 332824 7522.431511958
we are updating event count 333000
computed currlat 1.690056
Found match: {'tr

...

Exception in thread Thread-12 (_run):
Traceback (most recent call last):
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1073, in _bootstrap_inner
    self.run()
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/venv/lib/python3.12/site-packages/ipykernel/ipkernel.py", line 772, in run_closure
    _threading_Thread_run(self)
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1010, in run
    self._target(*self._args, **self._kwargs)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/data_parallel/DataParallelExecutionAlgorithm.py", line 119, in _run
    evaluation_manager.eval(events, matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/manager/SequentialEvaluationManager.py", line 32, in eval
    self.__eval_mechanism.eval(event_stream, pattern_matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/tree/evaluation

we are updating event count 635000
computed currlat 0.240304
Found match: {'tripduration': '191', 'starttime': 2019-01-26 19:09:51.183000, 'stoptime': 2019-01-26 19:13:02.364000, 'startstationid': '465', 'endstationid': '529', 'bikeid': '35741', 'eventid': 823050}
{'tripduration': '452', 'starttime': 2019-01-26 19:13:06.155000, 'stoptime': 2019-01-26 19:20:38.540000, 'startstationid': '529', 'endstationid': '111111', 'bikeid': '35741', 'eventid': 823138}


event count 635220 8154.154367541
computed currlat 0.240304
Found match: {'tripduration': '106', 'starttime': 2019-01-26 11:51:12.837000, 'stoptime': 2019-01-26 11:52:59.121000, 'startstationid': '3321', 'endstationid': '3315', 'bikeid': '33251', 'eventid': 807850}
{'tripduration': '407', 'starttime': 2019-01-26 11:52:59.756000, 'stoptime': 2019-01-26 11:59:47.256000, 'startstationid': '3315', 'endstationid': '111111', 'bikeid': '33251', 'eventid': 807935}


event count 635567 8154.837992291
computed currlat 0.240304
Found match: {'t

Exception in thread Thread-9 (_run):
Traceback (most recent call last):
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1073, in _bootstrap_inner
    self.run()
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/venv/lib/python3.12/site-packages/ipykernel/ipkernel.py", line 772, in run_closure
    _threading_Thread_run(self)
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1010, in run
    self._target(*self._args, **self._kwargs)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/data_parallel/DataParallelExecutionAlgorithm.py", line 119, in _run
    evaluation_manager.eval(events, matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/manager/SequentialEvaluationManager.py", line 32, in eval
    self.__eval_mechanism.eval(event_stream, pattern_matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/tree/evaluation/

computed currlat 0.240304
Found match: {'tripduration': '216', 'starttime': 2019-01-28 12:21:47.953000, 'stoptime': 2019-01-28 12:25:24.421000, 'startstationid': '426', 'endstationid': '82', 'bikeid': '28235', 'eventid': 871043}
{'tripduration': '303', 'starttime': 2019-01-28 12:25:25.376000, 'stoptime': 2019-01-28 12:30:28.727000, 'startstationid': '82', 'endstationid': '111111', 'bikeid': '28235', 'eventid': 871128}


event count 668775 8221.461255375
we are updating event count 669000
computed currlat 0.240304
Found match: {'tripduration': '169', 'starttime': 2019-01-28 12:44:57.703000, 'stoptime': 2019-01-28 12:47:47.344000, 'startstationid': '3454', 'endstationid': '3081', 'bikeid': '35387', 'eventid': 871600}
{'tripduration': '702', 'starttime': 2019-01-28 12:47:48.190000, 'stoptime': 2019-01-28 12:59:30.981000, 'startstationid': '3081', 'endstationid': '111111', 'bikeid': '35387', 'eventid': 871661}


event count 669030 8221.97057125
computed currlat 0.240304
Found match: {'trip

1455.136883